In [1]:
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
from collections import OrderedDict

In [2]:
# prevent scientific notation in dataframe, round to 2 decimal places
pd.set_option('display.float_format', lambda x: '%.2f' % x)
plt.style.use('seaborn-deep')

In [3]:
trials = 7
time_length=25
min_interest = 1
max_interest = 8
volatility=11
contributions = [i*10000 for i in [3, 4, 5, 6, 7, 8, 9, 10]]
principal = 0
interest_rates = np.arange(min_interest, max_interest+0.1, 1)

In [4]:
def run_trial(contribution=10000, principal=0, volatility=10, time_length=20):

    di = {}

    for rate in interest_rates:
        prices = np.zeros(time_length)
        prices[0] = principal

        for i in np.arange(1, time_length, 1):
            # last price + contribution, x interest, x random volatility factor
            prices[i] = (prices[i-1] + contribution) * (1 + rate/100) * (np.random.normal(1, volatility/100))

        di[rate] = prices

    return di

In [5]:
dat = {amount:[run_trial(contribution=amount, principal=principal, volatility=volatility) for i in range(trials)] for amount in contributions}

In [6]:
average_returns = []
# for each contribution amount, calculate return for each rate, averaged over all trials
for idx1, contrib in enumerate(contributions): # for each contribution amount
    this_contrib = []
    for idx2, all_trials in enumerate(dat[contrib]): # average over all trials
        this_trial = []
        for idx3, rates in enumerate(interest_rates): # for each rate
            this_trial.append(dat[contrib][idx2][rates][-1]) # just the ending value
        this_contrib.append(this_trial)
    average_returns.append(this_contrib)


In [7]:
average_returns = np.array(average_returns).mean(1) # average of dim2 (trials)
ar = pd.DataFrame(average_returns)

ar.columns = interest_rates
ar.columns.names = ['Rates']
ar.index = contributions
ar.index.names = ['Yearly Contributions']

own_contributions = [principal + contrib * time_length for contrib in contributions]
ar['Total Contributed'] = own_contributions

In [8]:
ar

Rates                       1.0        2.0        3.0        4.0        5.0  \
Yearly Contributions                                                          
30000                 680392.35  719003.94  669179.21 1045067.05  914208.50   
40000                 830649.95 1001500.00 1005847.26 1131227.03 1253337.24   
50000                1002717.30 1150779.79 1128912.41 1160285.64 1722661.28   
60000                1285554.75 1302313.31 1561713.68 1619442.32 1789249.89   
70000                1570867.49 1596408.60 1634376.47 2152451.68 2064830.10   
80000                2199935.28 1705646.92 1710485.36 2279376.15 2556375.32   
90000                2114928.26 2005861.96 2082509.46 2908641.45 2471273.57   
100000               2034787.74 2275918.01 2937393.78 3208549.56 2981889.05   

Rates                       6.0        7.0        8.0  Total Contributed  
Yearly Contributions                                                      
30000                1307822.07 1185079.76 1326281.97             750000  
40000                1396360.71 1459869.35 1876795.50            1000000  
50000                1831219.41 1739499.67 2102465.47            1250000  
60000                2704366.48 2036473.13 3013029.82            1500000  
70000                1945758.46 3065336.94 2793221.53            1750000  
80000                2528003.86 2664752.67 3420741.96            2000000  
90000                3665403.29 5238245.76 3500246.67            2250000  
100000               4219085.84 3928147.71 4736687.10            2500000

In [9]:
fig, axes = plt.subplots(len(contributions), figsize=((16, 40)), dpi=421)
plt.suptitle(f'Monte Carlo Simulation (n={trials}) of Possible Returns Over {time_length} Years at {volatility}% Volatility')

for idx, (contrib_key, contrib_value) in enumerate(dat.items()):
    for trial in contrib_value:
        for rate_key, rate_value in trial.items():
            sns.lineplot(data=rate_value, ax=axes[idx], label=f'At {rate_key}%: ${ar.loc[contrib_key, rate_key]:,.2f} Average Return')
        # reset colour cycle
        axes[idx].set_prop_cycle(None)

        # remove duplicates and put yearly contributions in the legend
        handles, labels = axes[idx].get_legend_handles_labels()
        by_label = OrderedDict(zip(labels, handles))
        axes[idx].legend(by_label.values(), by_label.keys(), title=f'${contrib_key:,.2f} Yearly Contribution\n')

In [ ]:
fig.savefig('simulations.svg', format='svg', transparent=False)